In [110]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
from collections import OrderedDict

In [111]:
# prevent scientific notation in dataframe, round to 2 decimal places
pd.set_option('display.float_format', lambda x: '%.2f' % x)
plt.style.use('seaborn-deep')

In [112]:
trials = 10000
time_length=25
min_interest = 1
max_interest = 8
volatility=11
contributions = [i*10000 for i in [3, 4, 5, 6, 7, 8, 9, 10]]
principal = 0
interest_rates = np.arange(min_interest, max_interest+0.1, 1)

In [113]:
def run_trial(contribution=10000, principal=0, volatility=10, time_length=20):

    di = {}

    for rate in interest_rates:
        prices = np.zeros(time_length)
        prices[0] = principal

        for i in np.arange(1, time_length, 1):
            # last price + contribution, x interest, x random volatility factor
            prices[i] = (prices[i-1] + contribution) * (1 + rate/100) * (np.random.normal(1, volatility/100))

        di[rate] = prices

    return di

In [114]:
dat = {amount:[run_trial(contribution=amount, principal=principal, volatility=volatility) for i in range(trials)] for amount in contributions}

In [115]:
average_returns = []
# for each contribution amount, calculate return for each rate, averaged over all trials
for idx1, contrib in enumerate(contributions): # for each contribution amount
    this_contrib = []
    for idx2, all_trials in enumerate(dat[contrib]): # average over all trials
        this_trial = []
        for idx3, rates in enumerate(interest_rates): # for each rate
            this_trial.append(dat[contrib][idx2][rates][-1]) # just the ending value
        this_contrib.append(this_trial)
    average_returns.append(this_contrib)


In [116]:
average_returns = np.array(average_returns).mean(1) # average of dim2 (trials)
ar = pd.DataFrame(average_returns)

ar.columns = interest_rates
ar.columns.names = ['Rates']
ar.index = contributions
ar.index.names = ['Yearly Contributions']

own_contributions = [principal + contrib * time_length for contrib in contributions]
ar['Total Contributed'] = own_contributions

In [117]:
ar

Rates                       1.0        2.0        3.0        4.0        5.0  \
Yearly Contributions                                                          
30000                 631209.33  696616.53  775470.05  861043.79  960062.06   
40000                 840909.63  936838.52 1034265.52 1151832.24 1273605.16   
50000                1050095.18 1170448.43 1292427.15 1435228.09 1597463.79   
60000                1264665.64 1402070.74 1547641.10 1719697.39 1934536.97   
70000                1466683.49 1632444.10 1807309.57 2009853.85 2248525.73   
80000                1683087.84 1871462.37 2072946.42 2292140.03 2577178.92   
90000                1894224.01 2102085.26 2326077.09 2587325.58 2877875.02   
100000               2098969.01 2329733.49 2587722.32 2878953.32 3209503.94   

Rates                       6.0        7.0        8.0  Total Contributed  
Yearly Contributions                                                      
30000                1069980.92 1196401.78 1345632.73             750000  
40000                1421497.75 1598740.38 1795643.79            1000000  
50000                1789866.77 1996264.10 2254091.36            1250000  
60000                2142968.79 2390987.48 2681181.63            1500000  
70000                2517344.62 2814773.48 3146356.93            1750000  
80000                2857082.20 3203692.84 3588009.29            2000000  
90000                3238437.22 3594939.73 4051835.81            2250000  
100000               3597679.81 3978546.06 4494154.61            2500000

In [118]:
fig, axes = plt.subplots(len(contributions), figsize=((16, 40)), dpi=421)
plt.suptitle(f'Monte Carlo Simulation (n={trials}) of Possible Returns Over {time_length} Years at {volatility}% Volatility')

for idx, (contrib_key, contrib_value) in enumerate(dat.items()):
    for trial in contrib_value:
        for rate_key, rate_value in trial.items():
            sns.lineplot(data=rate_value, ax=axes[idx], label=f'At {rate_key}%: ${ar.loc[contrib_key, rate_key]:,.2f} Average Return')
        # reset colour cycle
        axes[idx].set_prop_cycle(None)

        # remove duplicates and put yearly contributions in the legend
        handles, labels = axes[idx].get_legend_handles_labels()
        by_label = OrderedDict(zip(labels, handles))
        axes[idx].legend(by_label.values(), by_label.keys(), title=f'${contrib_key:,.2f} Yearly Contribution\n')

KeyboardInterrupt: 

In [66]:
fig.savefig('simulations.svg', format='svg', transparent=False)